In [ ]:
# Uncomment and run this cell if you're on Colab or Kaggle
# !git clone https://github.com/nlp-with-transformers/notebooks.git
# %cd notebooks
# from install import *
# install_requirements()

In [2]:
#hide
from utils import *
setup_chapter()

Using transformers v4.16.2
Using datasets v1.16.1


# Transformer Anatomy

## The Transformer Architecture

<img alt="transformer-encoder-decoder" caption="Encoder-decoder architecture of the transformer, with the encoder shown in the upper half of the figure and the decoder in the lower half" src="images/chapter03_transformer-encoder-decoder.png" id="transformer-encoder-decoder"/>

## The Encoder

<img alt="encoder-zoom" caption="Zooming into the encoder layer" src="images/chapter03_encoder-zoom.png" id="encoder-zoom"/>

### Self-Attention

<img alt="Contextualized embeddings" caption="Diagram showing how self-attention updates raw token embeddings (upper) into contextualized embeddings (lower) to create representations that incorporate information from the whole sequence" src="images/chapter03_contextualized-embedding.png" id="contextualized-embeddings"/>

#### Scaled dot-product attention

#hide

Copy and execute the following cell magic in a new cell to use `bertviz` in JupyterLab:

```python
%%javascript
require.config({
  paths: {
      d3: '//cdnjs.cloudflare.com/ajax/libs/d3/3.4.8/d3.min',
      jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
  }
});
```

In [7]:
#hide_output
from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

model_ckpt = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model = BertModel.from_pretrained(model_ckpt)
text = "time flies like an arrow"
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Sidebar: Demystifying Queries, Keys, and Values

### End sidebar

<img alt="Operations in scaled dot-product attention" height="125" caption="Operations in scaled dot-product attention" src="images/chapter03_attention-ops.png" id="attention-ops"/>

In [8]:
# hide
from transformers import AutoTokenizer
model_ckpt = "bert-base-uncased"
text = "time flies like an arrow"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)

In [12]:
inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False)
inputs.input_ids

tensor([[ 2051, 10029,  2066,  2019,  8612]])

In [9]:
from torch import nn
from transformers import AutoConfig

config = AutoConfig.from_pretrained(model_ckpt)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

In [13]:
inputs_embeds = token_emb(inputs.input_ids)
inputs_embeds.size()

torch.Size([1, 5, 768])

In [14]:
import torch
from math import sqrt 

query = key = value = inputs_embeds
dim_k = key.size(-1)
scores = torch.bmm(query, key.transpose(1,2)) / sqrt(dim_k)
scores.size()

torch.Size([1, 5, 5])

In [19]:
tenst = torch.tensor([[[1,2,3,4],[4,5,6,6],[7,8,9,9]]])
tenst.size()
summ = tenst.sum(dim=1)
#summ.size()
summ
# sum(dim=-1) 은 마지막 차원을 제거하고 합계를 계산한다. 행렬에서 한 행의 합계를 계산한다.
# sum(dim=1) 은 두번째 차원을 제거하고 합계를 계산한다. 행렬에서 한 열의 합계를 계산한다.

tensor([[12, 15, 18, 19]])

In [15]:
import torch.nn.functional as F

weights = F.softmax(scores, dim=-1)
weights.sum(dim=-1).size()


torch.Size([1, 5])

In [18]:
attn_outputs = torch.bmm(weights, value)
attn_outputs.shape

torch.Size([1, 5, 768])

In [26]:
def scaled_dot_product_attention(query, key, value):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    weights = F.softmax(scores, dim=-1)
    return torch.bmm(weights, value)

#### Multi-headed attention

<img alt="Multi-head attention" height="125" caption="Multi-head attention" src="images/chapter03_multihead-attention.png" id="multihead-attention"/>

In [22]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)

    def forward(self, hidden_state):
        print(self.v(hidden_state).size())
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state))
        return attn_outputs

In [23]:
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, embed_dim)

    def forward(self, hidden_state):
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

In [29]:
multihead_attn = MultiHeadAttention(config)
attn_output = multihead_attn(inputs_embeds)    
attn_output.size() 

torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])


torch.Size([1, 5, 768])

In [30]:
#hide_output
from bertviz import head_view
from transformers import AutoModel

model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)

sentence_a = "time flies like an arrow"
sentence_b = "fruit flies like a banana"

viz_inputs = tokenizer(sentence_a, sentence_b, return_tensors='pt')
attention = model(**viz_inputs).attentions
sentence_b_start = (viz_inputs.token_type_ids == 0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

head_view(attention, tokens, sentence_b_start, heads=[8])

Downloading:   0%|          | 0.00/420M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.dense.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


<IPython.core.display.Javascript object>

어제 여기 까지 했음

### The Feed-Forward Layer

In [16]:
class FeedForward(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
        self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
        self.gelu = nn.GELU()
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        
    def forward(self, x):
        x = self.linear_1(x)
        x = self.gelu(x)
        x = self.linear_2(x)
        x = self.dropout(x)
        return x

In [24]:
feed_forward = FeedForward(config)
ff_outputs = feed_forward(attn_outputs)
ff_outputs.size()

torch.Size([1, 5, 768])

### Adding Layer Normalization

<img alt="Transformer layer normalization" height="500" caption="Different arrangements of layer normalization in a transformer encoder layer" src="images/chapter03_layer-norm.png" id="layer-norm"/>

In [20]:
class TransformerEncoderLayer(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.layer_norm_1 = nn.LayerNorm(config.hidden_size)
        self.layer_norm_2 = nn.LayerNorm(config.hidden_size)
        self.attention = MultiHeadAttention(config)
        self.feed_forward = FeedForward(config)

    def forward(self, x):
        # Apply layer normalization and then copy input into query, key, value
        hidden_state = self.layer_norm_1(x)
        # Apply attention with a skip connection
        x = x + self.attention(hidden_state)
        # Apply feed-forward layer with a skip connection
        x = x + self.feed_forward(self.layer_norm_2(x))
        return x

In [27]:
encoder_layer = TransformerEncoderLayer(config)
inputs_embeds.shape, encoder_layer(inputs_embeds).size()

torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])


(torch.Size([1, 5, 768]), torch.Size([1, 5, 768]))

### Positional Embeddings

In [32]:
class Embeddings(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.token_embeddings = nn.Embedding(config.vocab_size, 
                                             config.hidden_size)
        self.position_embeddings = nn.Embedding(config.max_position_embeddings,
                                                config.hidden_size)
        self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12)
        self.dropout = nn.Dropout()

    def forward(self, input_ids):
        # Create position IDs for input sequence
        seq_length = input_ids.size(1)
        position_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0)
        # Create token and position embeddings
        token_embeddings = self.token_embeddings(input_ids)
        position_embeddings = self.position_embeddings(position_ids)
        print(token_embeddings)
        print(position_embeddings)
        # Combine token and position embeddings
        embeddings = token_embeddings + position_embeddings
        embeddings = self.layer_norm(embeddings)
        embeddings = self.dropout(embeddings)
        return embeddings

In [33]:
embedding_layer = Embeddings(config)
embedding_layer(inputs.input_ids).size()

tensor([[[-0.8323,  0.7805,  0.3645,  ..., -1.5666, -0.0355,  0.1408],
         [ 0.1449,  0.3193, -1.3829,  ..., -0.3596, -0.4661,  0.8142],
         [-0.0198,  1.5308, -1.1956,  ...,  0.9639, -1.2674, -1.0765],
         [-0.4198, -0.7659,  0.4640,  ...,  1.5171, -0.2096, -1.1181],
         [-0.0645,  2.2396,  0.7733,  ..., -1.6449, -0.7217,  0.8136]]],
       grad_fn=<EmbeddingBackward0>)
tensor([[[-0.2939,  0.4636,  1.1136,  ..., -1.1840, -0.1115, -1.4465],
         [-1.5186,  1.6395, -1.9488,  ...,  0.7483, -1.2306, -0.0941],
         [ 1.8605, -0.1015, -0.1482,  ...,  0.7742, -0.8125, -0.2458],
         [ 0.0514,  0.0079, -0.1614,  ...,  0.4107, -0.7075, -0.2663],
         [ 1.3030,  0.5119,  0.1418,  ...,  1.4717, -1.6339,  0.6720]]],
       grad_fn=<EmbeddingBackward0>)


torch.Size([1, 5, 768])

In [34]:
class TransformerEncoder(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.embeddings = Embeddings(config)
        self.layers = nn.ModuleList([TransformerEncoderLayer(config) 
                                     for _ in range(config.num_hidden_layers)])

    def forward(self, x):
        x = self.embeddings(x)
        for layer in self.layers:
            x = layer(x)
        return x

In [35]:
encoder = TransformerEncoder(config)
encoder(inputs.input_ids).size()

tensor([[[ 1.3528, -2.4168,  0.1415,  ..., -1.0666,  0.5990,  1.9212],
         [ 0.4474, -1.1099,  0.2213,  ...,  0.0219,  1.0011, -1.5072],
         [-0.7285,  1.1083,  1.4705,  ..., -0.6793,  0.8936, -2.5895],
         [-1.0796, -0.9615, -0.2639,  ..., -0.8183,  0.3023,  1.0621],
         [-0.2789, -0.5716, -0.2318,  ..., -0.1322, -0.3156, -0.9208]]],
       grad_fn=<EmbeddingBackward0>)
tensor([[[-0.4193,  0.7282, -1.3411,  ..., -0.0118, -0.2902,  0.4165],
         [-0.4328, -0.7616, -1.2248,  ...,  1.1613, -0.8171, -0.5552],
         [-0.1334, -0.0181, -2.1961,  ...,  0.5812, -0.5641, -0.7937],
         [-0.2232, -0.4326,  0.2767,  ...,  0.9339,  0.4972,  1.4369],
         [ 0.5539,  0.7540,  0.1306,  ..., -0.1952, -2.1643,  0.9680]]],
       grad_fn=<EmbeddingBackward0>)
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch

torch.Size([1, 5, 768])

### Adding a Classification Head

In [36]:
class TransformerForSequenceClassification(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.encoder = TransformerEncoder(config)
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        self.classifier = nn.Linear(config.hidden_size, config.num_labels)
        
    def forward(self, x):
        x = self.encoder(x)[:, 0, :] # select hidden state of [CLS] token
        x = self.dropout(x)
        x = self.classifier(x)
        return x

In [66]:
config.num_labels = 3
encoder_classifier = TransformerForSequenceClassification(config)
encoder_classifier(inputs.input_ids, None).size()

TypeError: forward() takes 2 positional arguments but 3 were given

In [64]:
encoder_classifier(inputs.input_ids)

NameError: name 'encoder_classifier' is not defined

## The Decoder

<img alt="Transformer decoder zoom" caption="Zooming into the transformer decoder layer" src="images/chapter03_decoder-zoom.png" id="decoder-zoom"/> 

In [37]:
seq_len = inputs.input_ids.size(-1)
mask = torch.tril(torch.ones(seq_len, seq_len)).unsqueeze(0)
mask[0]

tensor([[1., 0., 0., 0., 0.],
        [1., 1., 0., 0., 0.],
        [1., 1., 1., 0., 0.],
        [1., 1., 1., 1., 0.],
        [1., 1., 1., 1., 1.]])

In [38]:
scores.masked_fill(mask == 0, -float("inf"))

tensor([[[ 2.6094e+01,        -inf,        -inf,        -inf,        -inf],
         [-5.2554e-01,  2.6773e+01,        -inf,        -inf,        -inf],
         [-1.9568e-01,  6.7421e-01,  2.9411e+01,        -inf,        -inf],
         [-5.7881e-03,  1.5950e-01, -2.2478e-01,  2.7270e+01,        -inf],
         [ 1.5583e-01, -8.8622e-01, -2.9784e-01,  8.9608e-01,  2.9979e+01]]],
       grad_fn=<MaskedFillBackward0>)

In [43]:
def scaled_dot_product_attention(query, key, value, mask=None):
    dim_k = query.size(-1)
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    if mask is not None:
        scores = scores.masked_fill(mask == 0, float("-inf"))
    weights = F.softmax(scores, dim=-1)
    return weights.bmm(value)

In [59]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)

    def forward(self, hidden_state, mask):
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state), mask)
        return attn_outputs

In [60]:
class MaskedMultiHeadAttention(nn.Module):
    def __init__(self, config) -> None:
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, embed_dim)

    def forward(self, hidden_state, mask):
        x = torch.cat([h(hidden_state, mask) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

In [61]:
class EncoderDecoderAttention(nn.Module):
    def __init__(self, config) -> None:
        super().__init__()
        
        


    def forward(self, hidden_state, encoder_output, mask):
        attn_outputs = scaled_dot_product_attention(
            hidden_state, encoder_output, encoder_output, mask)
        return attn_outputs

In [62]:
class TransformerDecoderLayer(nn.Module):
    def __init__(self, config) -> None:
        super().__init__()
        self.layer_norm_1 = nn.LayerNorm(config.hidden_size)
        self.layer_norm_2 = nn.LayerNorm(config.hidden_size)
        self.layer_norm_3 = nn.LayerNorm(config.hidden_size)
        self.attention = MaskedMultiHeadAttention(config)
        self.encoder_decoder_attention = EncoderDecoderAttention(config)
        self.feed_forward = FeedForward(config)

    def forward(self, x, encoder_output, mask):
        hidden_state = self.layer_norm_1(x)
        x = x + self.attention(hidden_state, mask)
        x = self.layer_norm_2(x)
        x = x + self.encoder_decoder_attention(x, encoder_output, mask)
        x = self.layer_norm_3(x)
        x = x + self.feed_forward(x)
        return x

In [63]:
decoder_layer = TransformerDecoderLayer(config)
inputs_embeds.shape, decoder_layer(inputs_embeds, encoder(inputs.input_ids), mask).size()

tensor([[[ 1.3528, -2.4168,  0.1415,  ..., -1.0666,  0.5990,  1.9212],
         [ 0.4474, -1.1099,  0.2213,  ...,  0.0219,  1.0011, -1.5072],
         [-0.7285,  1.1083,  1.4705,  ..., -0.6793,  0.8936, -2.5895],
         [-1.0796, -0.9615, -0.2639,  ..., -0.8183,  0.3023,  1.0621],
         [-0.2789, -0.5716, -0.2318,  ..., -0.1322, -0.3156, -0.9208]]],
       grad_fn=<EmbeddingBackward0>)
tensor([[[-0.4193,  0.7282, -1.3411,  ..., -0.0118, -0.2902,  0.4165],
         [-0.4328, -0.7616, -1.2248,  ...,  1.1613, -0.8171, -0.5552],
         [-0.1334, -0.0181, -2.1961,  ...,  0.5812, -0.5641, -0.7937],
         [-0.2232, -0.4326,  0.2767,  ...,  0.9339,  0.4972,  1.4369],
         [ 0.5539,  0.7540,  0.1306,  ..., -0.1952, -2.1643,  0.9680]]],
       grad_fn=<EmbeddingBackward0>)
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch.Size([1, 5, 64])
torch

(torch.Size([1, 5, 768]), torch.Size([1, 5, 768]))

### Sidebar: Demystifying Encoder-Decoder Attention

### End sidebar

## Meet the Transformers

### The Transformer Tree of Life

<img alt="Transformer family tree" caption="An overview of some of the most prominent transformer architectures" src="images/chapter03_transformers-compact.png" id="family-tree"/>

### The Encoder Branch

### The Decoder Branch

### The Encoder-Decoder Branch

## Conclusion